In [72]:
import pandas as pd
import seaborn as sns
import os
import matplotlib.pyplot as plt

In [73]:
agg_df = pd.DataFrame()

workdir_path = 'wos_downloads/aggregated'
for root, dirs, files in os.walk(workdir_path):
    for filename in files:
        if 'analyze_' in filename:
            path=os.path.join(root, filename)
            with open(os.path.join(root, 'query.txt'),'r') as f:
                query = f.readline()
            chunk = pd.read_csv(path, sep='\t')[["Publication Years","Record Count"]]
            chunk["name"] = filename.replace(".txt","")
            chunk["query"] = query
            agg_df = pd.concat([chunk,agg_df],ignore_index=True)

In [74]:
agg_df["region"] = agg_df["query"].apply(lambda x: "EU+China" if "CU" in x else "Global")
agg_df["kw_token"] = agg_df["query"].apply(lambda x: x.split("TS=(")[-1].split(")")[0])
agg_df["kw_token"] = agg_df["kw_token"].apply(lambda x: "OR COMPOSITE" if " OR " in x else x)

In [83]:
agg_df = agg_df[~agg_df["Record Count"].isna()]

In [62]:
agg_df.groupby("query",as_index=False)["Record Count"].sum()

query  Record Count
0    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...         972.0
1    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...         451.0
2    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...          12.0
3    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...           5.0
4    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...        2631.0
..                                                 ...           ...
275     TS=("ubiquitous computing") AND PY=(2011-2022)        3655.0
276       TS=("unstructured data*") AND PY=(2011-2022)        3386.0
277  TS=("unsupervised deep learning") AND PY=(2011...         728.0
278          TS=("word embedding*") AND PY=(2011-2022)        7068.0
279             TS=("word vector*") AND PY=(2011-2022)        1747.0

[280 rows x 2 columns]

In [63]:
# agg_df = agg_df[agg_df["Publication Years"].str.startswith("20", na=False)].copy()
# agg_df["Publication Years"] = agg_df["Publication Years"].astype(int)
# agg_df[((agg_df["Publication Years"]>2010) & (agg_df["Publication Years"]<2023))]

In [84]:
agg_df["Publication Years"].value_counts()

Publication Years
2022    314
2019    305
2021    305
2020    302
2018    296
2017    287
2016    281
2015    271
2014    258
2013    251
2012    233
2011    224
2023     52
2017      4
2014      4
2019      4
2021      4
2018      4
2020      4
2022      4
2016      3
2015      3
2013      3
2012      3
2011      3
2023      2
Name: count, dtype: int64

In [85]:
agg_df.to_excel(r'C:\Users\radvanyi\PycharmProjects\ZSI_analytics\WOS\wos_processed_data\query_yearly_agg.xlsx', index=False)